In [1]:
# Ref
### https://www.nature.com/articles/s41596-020-0336-2
### https://scenic.aertslab.org/tutorials/
### https://github.com/aertslab/SCENICprotocol/blob/master/notebooks/PBMC10k_SCENIC-protocol-CLI.ipynb

# import dependencies
#import os
import numpy as np
import pandas as pd
import scanpy as sc
import loompy as lp
import sklearn
import os
#from MulticoreTSNE import MulticoreTSNE as TSNE

import session_info
session_info.show()

#!~/.conda/envs/yuan2/bin/pyscenic



# set a working directory
wdir = "network_FGF8/"
os.chdir( wdir )


# # path to loom file with basic filtering applied (this will be created in the "initial filtering" step below). Optional.
f_loom_path_scenic = wdir+"B_SCENIC/output/filtered_scenic.loom"
output_adjaceny = wdir+"B_SCENIC/output/adjacencies.csv"
output_regulon = wdir+"B_SCENIC/output/regulons.csv"
output_auc_mtx = wdir+"B_SCENIC/output/auc_mtx.csv"
THREADS=20

In [15]:

# 1. SCENIC analysis: predict activated regulons

### 1. Gene regulatory network inference and generation of co-expressiom modules from expression matrix

# Phase Ia GRN inference using the GRNBoost2 algorithm

#For this step the CLI version of SCENIC is used. This step can be deployed on an High performance computing system. We use the counts matrix (without log transformation or further processing) from the loom file we wrote earier. OUTPUT: list of adjancencies between a TF and its targets stored in ADACENCIES_FNAME

# transcription factors list
f_tfs = "/scratch/yuan/pyscenicdata/hs_hgnc_curated_tfs.txt" # human
# f_tfs = "/ddn1/vol1/staging/leuven/stg_00002/lcb/cflerin/resources/allTFs_dmel.txt" # drosophila
# f_tfs = "/ddn1/vol1/staging/leuven/stg_00002/lcb/cflerin/resources/allTFs_mm.txt"   # mouse
# tf_names = load_tf_names( f_tfs )

# f_loom_path_scenic: This dataset has been filtered, but not processed
!~/.conda/envs/yuan2/bin/pyscenic grn {f_loom_path_scenic} {f_tfs} -o {output_adjaceny} \
    --num_workers { THREADS }




2023-02-24 16:32:23,387 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2023-02-24 16:32:25,528 - pyscenic.cli.pyscenic - INFO - Inferring regulatory networks.
/home/zjr863/.conda/envs/yuan2/lib/python3.8/site-packages/distributed/node.py:181: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 45527 instead
  warnings.warn(
preparing dask client
parsing input
creating dask graph
20 partitions
computing dask graph
not shutting down client, client was created externally
finished

2023-02-24 18:01:58,361 - pyscenic.cli.pyscenic - INFO - Writing results to file.


In [2]:
### 2. Regulon prediction aka cisTarget from CLI (Find enriched motifs for a gene signature and opitionally prune targets from this signature based on cis-regulatory cues)
#For this step the CLI version of SCENIC is used. This step can be deployed on an High Performance Computing system.
#Output: List of adjacencies between a TF and its targets stored in MOTIFS_FNAME
import glob
# ranking databases
f_db_glob = "/scratch/yuan/pyscenicdata/*feather"
f_db_names = ' '.join( glob.glob(f_db_glob) )
print(f_db_names)

# motif databases (motifs of TFs)
f_motif_path = "/scratch/yuan/pyscenicdata/motifs-v9-nr.hgnc-m0.001-o0.0.tbl"

#f_loom_path_scenic: this loom file is like counts.tsv
!~/.conda/envs/yuan2/bin/pyscenic ctx {output_adjaceny} \
  {f_db_names} \
  --annotations_fname {f_motif_path} \
  --expression_mtx_fname {f_loom_path_scenic} \
  --mode "dask_multiprocessing" \
  --output {output_regulon} \
  --mask_dropouts \
  --num_workers { THREADS }
#reg.csv: is the direct target output (regulon)
#f_loom_path_scenic: This dataset has been filtered, but not processed

/scratch/yuan/pyscenicdata/hg19-500bp-upstream-10species.mc9nr.feather /scratch/yuan/pyscenicdata/hg19-500bp-upstream-7species.mc9nr.feather /scratch/yuan/pyscenicdata/hg19-tss-centered-10kb-10species.mc9nr.feather /scratch/yuan/pyscenicdata/hg19-tss-centered-10kb-7species.mc9nr.feather /scratch/yuan/pyscenicdata/hg19-tss-centered-5kb-10species.mc9nr.feather /scratch/yuan/pyscenicdata/hg19-tss-centered-5kb-7species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-500bp-upstream-10species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-500bp-upstream-7species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-tss-centered-10kb-10species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-tss-centered-10kb-7species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-tss-centered-5kb-10species.mc9nr.feather /scratch/yuan/pyscenicdata/mm9-tss-centered-5kb-7species.mc9nr.feather

2023-02-24 18:05:09,160 - pyscenic.cli.pyscenic - INFO - Creating modules.

2023-02-24 18:05:11,212 - pyscenic.cli.pyscenic - INFO - Loadin

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




2023-02-24 18:32:02,131 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for ZNF658 could be mapped to hg19-tss-centered-10kb-7species.mc9nr. Skipping this module.
[####################################    ] | 91% Completed | 23min 22.9s
2023-02-24 18:32:02,186 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF296 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[####################################    ] | 91% Completed | 23min 23.0s
2023-02-24 18:32:02,242 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF684 could be mapped to hg19-500bp-upstream-10species.mc9nr. Skipping this module.

2023-02-24 18:32:02,313 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF687 could be mapped to hg19-500bp-upstream-10species.mc9nr. Skipping this module.
[####################################    ] | 91% Completed | 23min 23.1s
2023-02-24 18:32:02,379 - pyscenic.transform - WARNING - Less than 80% of 

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[####################################### ] | 99% Completed | 28min 44.4s
2023-02-24 18:37:23,649 - pyscenic.transform - WARNING - Less than 80% of the genes in NR3C1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed | 28min 44.5s
2023-02-24 18:37:23,738 - pyscenic.transform - WARNING - Less than 80% of the genes in NR3C2 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed | 28min 46.7s
2023-02-24 18:37:25,895 - pyscenic.transform - WARNING - Less than 80% of the genes in NR4A1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2023-02-24 18:37:25,974 - pyscenic.transform - WARNING - Less than 80% of the genes in NR4A2 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[####################################### ] | 99% Completed | 28min 46.8s
2023-02-24 

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [3]:
### 3. aucell: quantify activity of gene signatures/regulons across single cells
#f_loom_path_scenic: this loom file is like counts.tsv
!~/.conda/envs/yuan2/bin/pyscenic aucell \
  {f_loom_path_scenic} \
  {output_regulon} \
  --output {output_auc_mtx} \
  --num_workers { THREADS }
  


2023-02-24 18:39:32,689 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2023-02-24 18:39:34,817 - pyscenic.cli.pyscenic - INFO - Loading gene signatures.
Create regulons from a dataframe of enriched features.
Additional columns saved: []

2023-02-24 18:41:02,406 - pyscenic.cli.pyscenic - INFO - Calculating cellular enrichment.

2023-02-24 18:41:25,252 - pyscenic.cli.pyscenic - INFO - Writing results to file.


In [4]:
import session_info
session_info.show()